# Interactive data visualization in Python: Geopandas
---

## Overview
   
Within this notebook, we will cover:

1. Browser-based interactive maps of point-based data 
1. [Geopandas](https://geopandas.org/en/stable/)

## Prerequisites
| Concepts | Importance | Notes |
| --- | --- | --- |
| [Cartopy Intro](https://foundations.projectpythia.org/core/cartopy/cartopy.html) | Required | Projections and Features |
| [Pandas](https://foundations.projectpythia.org/core/pandas.html) | Required | Tabular Datasets |

- **Time to learn**: 20 minutes
---

All of the graphics we have generated so far in the class have been *static*. In other words, they exist "as-is" ... there is no way to interact with them. While this is fine, and even preferable, for traditional publication figures and websites, it would be nice to be able to produce *dynamic* figures ... which one can zoom into/out of, pan around ... similar to, say, Google Maps.<br>
<br><hr>
We have previously displayed real-time NYS Mesonet observations on a static map, using Pandas, Cartopy, and Matplotlib. Now, let's make an *interactive* map ... for that, we will leverage the Geopandas Python package. 

## Imports

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from cartopy import crs as ccrs
from cartopy import feature as cfeature
import geopandas as gpd

### Read in the most recent set of NYSM observations

In [ ]:
nysm_latest = pd.read_csv('https://www.atmos.albany.edu/products/nysm/nysm_latest.csv')

In [ ]:
nysm_latest

Make our Pandas `Dataframe` *geo-aware*. To do this, we create a Geopandas Dataframe. It adds a `Geometry` column, which may consist of shapes or points. The NYSM locations are points, so that's what we'll use to instantiate the Geometry column.

In [ ]:
gdf = gpd.GeoDataFrame(nysm_latest,geometry=gpd.points_from_xy(nysm_latest.lon,nysm_latest.lat))

In [ ]:
gdf

Note that `geometry` appears as a new column (`Series`). 

We can interactively `explore` this Dataframe as a map in the browser!

In [ ]:
gdf.explore()

Well ... we have an interactive frame ... and it looks like New York State ... but where is the interactive map?? 

We still have a little more work to do:

While the points certainly look like latitude and longitudes, we need to explicitly assign a projection to the Dataframe before we can view it on a map. One way is to assign a coordinate reference system code, via [EPSG](https://epsg.io) ... in this case, [EPSG 4326](https://epsg.io/4326).

Note the arguments to `set_crs`:

1. `epsg = 4326`: Assign the specified CRS
1. `inplace = True`: The `gdf` object is updated without the need to assign a new dataframe object
1. `allow_override = True`: If a CRS had previously been applied, override with the EPSG value specified.

In [ ]:
gdf.set_crs(epsg=4326, inplace=True, allow_override=True)

Now, let's try the `explore` function again!

In [ ]:
gdf.explore()

We can pan, zoom, and hover over each point ... hovering shows the values of all the columns in the `Dataframe`.

Now, let's select just one column from the Dataframe and explore once again.

In [ ]:
gdf.explore(column='temp_2m [degC]')

By default, passing in one column of numerical values will color-code each value!

### Explore the most recent worldwide METARs

In [ ]:
worldMetar = pd.read_csv("https://www.atmos.albany.edu/products/metarCSV/world_metar_latest.csv", sep='\s+')

In [ ]:
worldMetar.rename(columns = {'SLAT':'lat','SLON':'lon'},inplace=True)

Examine the `dataframe`

In [ ]:
worldMetar

We have several stations at the end of the `Dataframe` whose latitudes and longitudes (and elevations) are **-9999.00**. These denote stations whose coordinates are not set in the underlying data source. We need to eliminate them in order for the geolocation to work properly.

In [ ]:
lat, lon = worldMetar.lat, worldMetar.lon

In [ ]:
worldMetar = worldMetar[(lat>-900) | (lon>-900)].reset_index(drop=True)

In [ ]:
worldMetar

Now, we can proceed with creating the Geopandas dataframe.

In [ ]:
gdfWorldMetar = gpd.GeoDataFrame(worldMetar,geometry=gpd.points_from_xy(worldMetar.lon,worldMetar.lat))

In [ ]:
gdfWorldMetar

In [ ]:
gdfWorldMetar.set_crs(epsg=4326, inplace=True, allow_override=True)

In [ ]:
gdfWorldMetar.explore()

<div class="alert alert-info"><b>Note: </b> Most of the non-US data is not available until approximately 15 minutes past each hour. If you do not see many worldwide stations, try re-reading the data file after that point in the hour.</div>

<div class="alert alert-warning"><b>Exercise: </b> Create a color-coded map from one variable in the dataset.</div>

In [ ]:
# Write your code here
gdfWorldMetar.explore(column='TMPC')

<div class="alert alert-danger">Were you surprised by your result? How might you make it look better?</div>

Follow a similar procedure as when we eliminated rows with latitudes or longitudes that equaled -9999.0. However, let's save some time by applying the test on the GeoPandas Dataframe, rather than on the original Pandas Dataframe.

In [ ]:
var = gdfWorldMetar.TMPC

In [ ]:
gdfWorldMetar = gdfWorldMetar[(var>-900)].reset_index(drop=True)

In [ ]:
gdfWorldMetar.explore(column='TMPC')